Week 3

Add News Titles/headlines for the prediction


<h1>In Progress</h1>

-currently added the api and be able to convert the json response to dataframe

-next week plan to add that to the LSTM model

In [ ]:
#Stock Price Prediction And Forecasting Using Stacked LSTM- Deep Learning

In [1]:
import pandas_datareader as pdr
#using tiingo library
key="08b78fbc98302e995956e2d3b5b8f3c0296d32cc"

I choose these companies because I know them or I read news about them. 
There are no particular reasons

In [2]:

stock = "BURL"#"EW"#"SYK"#"BACHF"#"NTTYY"#"INTC"#"DIS"#"TSLA"#"KEY"#"MSI"#"NVDA"#"AAPL"#"COST"#"AMZN"#"RIVN"#"GLD"#"RPRX"#"WDAY"#"CVX"#"FND"
#"ADBE"#"AAPL"#TDS"#"CLVT"#"RPRX"#"T"#"PHUN"#"ARDX"#"HPQ"#"CLVT"#"LGIH"#"FB"#"ORCL"#"MSFT"#"TDS"#"AMD"#"TM"#"DELL"#"COST"#"ABC"#"ABBV"
df = pdr.get_data_tiingo(stock, api_key=key)

In [3]:
df.to_csv(f'{stock}.csv')

In [4]:
import pandas as pd

df = pd.read_csv(f'{stock}.csv')


In [5]:
#Getting the start date of the stock data
import datetime

start_date=df.iloc[0]['date']

#start_date = datetime.datetime(start_date.year, start_date.month, start_date.day)
start_date = start_date.split(' ')
start_date = start_date[0]
start_date #type str

'2016-12-05'

In [6]:
#df.tail()

#Getting the end date of the stock data

end_date=df.iloc[len(df)-1]['date']
#start_date = datetime.datetime(start_date.year, start_date.month, start_date.day)
end_date = end_date.split(' ')
end_date = end_date[0]

end_date #type str

'2021-12-03'

In [7]:
from datetime import datetime

#Convert str format date to datetime object for easy calculation
def str_to_date(strdate):
    return datetime.strptime(strdate, '%Y-%m-%d')

#start_date = str_to_date(start_date)


In [8]:
#Convert datetime object to str for easy documentation
def date_to_str(datet):
    return datet.strftime('%m/%d/%Y')

#date_to_str(start_date)

GoogleNews API cannot provide headlines from the past date without a search

Then, I try NewsAPI. However, to acquire data from time range as far as 2016 will require pay membership.  

Last, I try the NewYorkTime API which allow access to past data and return the month of news

In [ ]:
#from GoogleNews import GoogleNews

#from datetime import timedelta
'''
googlenews = GoogleNews(lang='en')
current_day = start_date
next_day = date_to_str(str_to_date(start_date) + +timedelta(days=1)) 
googlenews.set_time_range(start_date,next_day)
'''

In [ ]:
#googlenews.search('finance')
#googlenews.get_texts()
#results = googlenews.results(sort=True)
#results

In [9]:
from pynytimes import NYTAPI

#New York Times API
nyt = NYTAPI("9xQE7W9DGO8r6GT8SwCdSTDqEVQTjdO4", parse_dates=True)

In [11]:
#Use pickle library for easy access and store
# 
# Since all news from each month will be the same, so data can be reuse 

import pickle
def save_net(savedfile,path):
    with open(path, 'wb') as f:
        pickle.dump(savedfile, f)
    #print(f'Pickle file saved for Forum {forum_id} at {path}...')
    return path

def get_net(path):
    with open(path, 'rb') as f:
        load = pickle.load(f)
        #print('retrieved!')
    return load


In [12]:
#Return filename in a specific format 
#so I can check if it exist in the file system

def get_file_name(date):
    current = date_to_str(date)
    current = current.split("/")
    current_m, current_yr = current[0],current[2]
    filename = f'{current_m}_{current_yr}_news.pckl'
    #('%m/%d/%Y')
    return filename

In [ ]:
from datetime import timedelta
from dateutil.relativedelta import relativedelta
import os.path
from os import path

#NYT API only need month and year
#To ensure the accuracy of the date, I reset the first date to the first day of the month
#Avoiding complcation in the month of Feburary
current_date = str_to_date(start_date).replace(day=1)
a_month = relativedelta(months=1) 

#request achieve news only if it does not already exist in the local path
while current_date <=  str_to_date(end_date):
    fn = get_file_name(current_date)
    if not path.isfile(fn):
        newsdata = nyt.archive_metadata(
            current_date
        )
        save_net(newsdata,fn)
    
    current_date = current_date + a_month

The following is testing on a single file that contains news from December of 2016

In [13]:
#get the news
news_result = get_net('12_2016_news.pckl')
#print(len(news_result))
news_result

[{'abstract': 'Mr. Trump’s surprise announcements and impulsive gestures have brought into sharp focus the compulsively theatrical style he will bring to the Oval Office.',
  'web_url': 'https://www.nytimes.com/2016/11/30/us/politics/donald-trump-white-house-cabinet.html',
  'snippet': 'Mr. Trump’s surprise announcements and impulsive gestures have brought into sharp focus the compulsively theatrical style he will bring to the Oval Office.',
  'lead_paragraph': 'It began at dawn, with a Twitter post about flag-burning.',
  'print_section': 'A',
  'print_page': '20',
  'source': 'The New York Times',
  'multimedia': [{'rank': 0,
    'subtype': 'xlarge',
    'caption': None,
    'credit': None,
    'type': 'image',
    'url': 'images/2016/12/01/us/01showman1/01showman1-articleLarge.jpg',
    'height': 400,
    'width': 600,
    'subType': 'xlarge',
    'crop_name': 'articleLarge',
    'legacy': {'xlarge': 'images/2016/12/01/us/01showman1/01showman1-articleLarge.jpg',
     'xlargewidth': 

In [17]:
import pandas as pd

#Convert the json file into dataframe for easier data process

headline_df = pd.DataFrame(columns={'date','headlines'})

data_list = []
for x in news_result:
    #current_date = date_to_str(x['pub_date']) #str
    current_date = date_to_str(x['pub_date']) #datetime
    day_headline = (x['headline']['main']) 
    if day_headline == '':
        break
    container = {'date':current_date,'headlines':day_headline}
    data_list.append(container)


    #if len(data_list) == 5: 
    #    break


headline_df = pd.DataFrame(data_list)
headline_df


date                                          headlines
0     12/01/2016  Trump, a Free-Form Leader, Experiments and Inv...
1     12/01/2016      Guggenheim Helsinki Museum Plans Are Rejected
2     12/01/2016  Recount Bids in 3 States Seem the Longest of L...
3     12/01/2016     Records of Bill de Blasio's Helicopter Flights
4     12/01/2016  Mayor de Blasio’s Trips by Police Helicopter R...
...          ...                                                ...
4962  12/31/2016  U.N. Encourages, but Stops Short of Endorsing,...
4963  12/31/2016  F. Ross Johnson, Symbol of ’80s Corporate Exce...
4964  12/31/2016                              Rolling in the Aisles
4965  12/31/2016  Chief Justice Salutes Trial Judges for Tacklin...
4966  12/31/2016  Terrorist Attack at Nightclub in Istanbul Kill...

[4967 rows x 2 columns]

Since each date have more than one news, I would want to group it by date when put it in my machine learning model

In [18]:

#Grouping the headlines by date

headline_df = headline_df.groupby('date')
headline_df.first()

headlines
date                                                         
12/01/2016  Trump, a Free-Form Leader, Experiments and Inv...
12/02/2016  Russian Spacecraft Carrying Supplies Burns Up ...
12/03/2016  It’s Trump’s Economy Now. What Will He Do With...
12/04/2016  Jill Stein’s Pennsylvania Recount Effort Is De...
12/05/2016  Shadows Fall and Jaws Drop for a Jolly Green I...
12/06/2016                  Dylann Roof’s Letter to the Court
12/07/2016                                               Aska
12/08/2016  Wary Corporate Chiefs Keep an Ear Tuned to Tru...
12/09/2016  U.N. Says Nearly One in Four Children Live in ...
12/10/2016  ‘Restaurant Recession’ From Health Care Act? L...
12/11/2016          Bob Dylan’s Nobel Prize Acceptance Speech
12/12/2016                        ‘Could You Patent the Sun?’
12/13/2016  Cathedral Bombing in Cairo Leaves Egypt Alarme...
12/14/2016     Court Debates Which Cosby Accusers May Testify
12/15/2016         Fox News Names New Head of Human Resources
12/16/2016                       Film Series in NYC This Week
12/17/2016  Prosecutors Drop Inquiry Into Charles Hynes, F...
12/18/2016  Trump Ends ‘Thank You’ Tour on Familiar Theme:...
12/19/2016  Hungry, Thirsty and Bloodied in Battle to Reta...
12/20/2016  Book Deal for Pantsuit Nation, Facebook Page S...
12/21/2016  Nielsen Acquires Gracenote, Highlighting the V...
12/22/2016  In Kansas, Where Republicans and Fiscal Woes R...
12/23/2016                          What’s New in NYC Theater
12/24/2016  Businesses Near Trump Tower Say Security Is St...
12/25/2016  Giants Idly Clinch Playoff Spot, Through a Tam...
12/26/2016      Treasury Auctions Set for the Week of Dec. 26
12/27/2016  California, at Forefront of Climate Fight, Won...
12/28/2016   Art That’s Disposable, but by No Means Throwaway
12/29/2016  Video Blogger Who Tested Singapore’s Limits Se...
12/30/2016                   Art and Museums in NYC This Week
12/31/2016  Cub Scouts Kick Out Transgender Boy in New Jersey

The rest are same as last week
I have not have the chance to finish adding the news dataframes to the model yet

Our next goal is combining dataframe together
For example, it should contain "date, close price, headlines..."
Then I will apply LSTM to predict the close price

In [ ]:
#value to predict
df_closePrice = df.reset_index()['close']

In [ ]:
df_closePrice.shape

In [ ]:
import matplotlib.pyplot as plt
plt.plot(df_closePrice)

In [ ]:
#LSTM is sensitive to the scale 
import numpy as np
from sklearn.preprocessing import MinMaxScaler

# use MinMax scalar to transform the value between 0 and 1
scaler=MinMaxScaler(feature_range=(0,1))
df_closePrice=scaler.fit_transform(np.array(df_closePrice).reshape(-1,1))



In [ ]:
#converted to array of values between 0 and 1 
df_closePrice 

In [ ]:
# make train test split
split_percentage = 0.65
training_size = int(len(df_closePrice)*split_percentage)
test_size=len(df_closePrice)-training_size
#split the dataframe
train_data = df_closePrice[0:training_size,:]
test_data = df_closePrice[training_size:len(df_closePrice),:1]

print(len(train_data))
print(len(test_data))

In [ ]:

# This method is use to separate the data in the order of its timeline
	#for example, 
	#Train: 1, 2, 4, 1, 5, 6 
	#will return 1, 2, 4, 1 (train_x); 5, 6 (train_y)
#This will preserve the time in the model,
#so we cannot use the future to predict the past
def create_dataset(dataset, time_step=1):
	x, y = [], []
	for i in range(len(dataset)-time_step-1):
		a = dataset[i:(i+time_step), 0]   ###i=0, 0,1,2,3-----99   100 
		x.append(a)
		y.append(dataset[i + time_step, 0])
	return np.array(x), np.array(y)

In [ ]:
# reshape into X=t,t+1,t+2,t+3 and Y=t+4

#change from 100 to 150

time_step = 150 #more the better; train test split

train_x, train_y = create_dataset(train_data, time_step)
test_x, test_y = create_dataset(test_data, time_step)

In [ ]:
print(train_x)

In [ ]:
print(train_x.shape), print(train_y.shape)
print(test_x.shape), print(test_y.shape)

In [ ]:
#reshape input 
train_x =train_x.reshape(train_x.shape[0],train_x.shape[1] , 1)
test_x = test_x.reshape(test_x.shape[0],test_x.shape[1] , 1)

In [ ]:
### Create the Stacked LSTM model
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import LSTM


In [ ]:
#Creating nested LSTM model
from tensorflow.keras.layers import Bidirectional
from tensorflow.keras.layers import Dropout

model = Sequential()

#change layer input from 100 to 150

#CHANGE 
    #Add Bidirectional LSTM layer
    #Add Dropout regularization
    #Add activation functio nin each layer

#parameter obtain from the paper
    #http://cs230.stanford.edu/projects_winter_2020/reports/32066186.pdf

model.add(Bidirectional(LSTM(50,return_sequences=True,activation="tanh"),input_shape=(150,1)))
model.add(Bidirectional(LSTM(50,return_sequences=True)))
model.add(Bidirectional(LSTM(50,dropout=0.2)))
#model.add(Bidirectional(LSTM(50,activation="tanh")))
#add sigmoid
model.add(Dense(1, activation='sigmoid'))

model.compile(loss='mean_squared_error',optimizer='adam')



In [ ]:
model.summary()

In [ ]:
model.fit(train_x,train_y,validation_data=(test_x,test_y),epochs=100,batch_size=64,verbose=1)


In [ ]:
import tensorflow as tf

train_predict = model.predict(train_x)
test_predict = model.predict(test_x)

In [ ]:
#Transform back to original data range
#from (0,1) back to original range

train_predict=scaler.inverse_transform(train_predict)
test_predict=scaler.inverse_transform(test_predict)

In [ ]:
### Calculate RMSE performance metrics
import math
from sklearn.metrics import mean_squared_error

#result for training dataset
math.sqrt(mean_squared_error(train_y,train_predict))


In [ ]:
### Test Data RMSE
math.sqrt(mean_squared_error(test_y,test_predict))

In [ ]:
train_predict.shape

In [ ]:
### Plotting 
# shift train predictions for plotting

#CHANGE look back change from 100 to 150

look_back=150
trainPredictPlot = np.empty_like(df_closePrice)
trainPredictPlot[:, :] = np.nan
trainPredictPlot[look_back:len(train_predict)+look_back, :] = train_predict
# shift test predictions for plotting
testPredictPlot = np.empty_like(df_closePrice)
testPredictPlot[:, :] = np.nan
testPredictPlot[len(train_predict)+(look_back*2)+1:len(df_closePrice)-1, :] = test_predict
# plot baseline and predictions
plt.plot(scaler.inverse_transform(df_closePrice))
plt.plot(trainPredictPlot)
plt.plot(testPredictPlot)
plt.show()

#test predict is green
#blue is the whole data set
#orange is the train predict

In [ ]:
#prediction

#Change look
start_point = len(test_data) -look_back
#use 100 data poin to predict
x_input=test_data[start_point:].reshape(1,-1)
x_input.shape



In [ ]:
temp_input=list(x_input)
temp_input=temp_input[0].tolist() #all the test_data with previous 100 data point

In [ ]:
# demonstrate prediction for next 30 days
from numpy import array

lst_output=[]
n_steps=150
i=0

# CHANGE
date_predict = 30
while(i<date_predict):
    
    if(len(temp_input)>150):
        #if more than 150 data point shift the list to contain only 150 datapoint

        #print(temp_input)
        x_input=np.array(temp_input[1:]) #shifting one poistion to the right
        print("{} day input {}".format(i,x_input))
        x_input=x_input.reshape(1,-1)
        x_input = x_input.reshape((1, n_steps, 1))
        #print(x_input)
        y_pred = model.predict(x_input, verbose=0)
        print("{} day output {}".format(i,y_pred))
        temp_input.extend(y_pred[0].tolist())
        temp_input=temp_input[1:]
        #print(temp_input)
        lst_output.extend(y_pred.tolist())
        i=i+1
    else:
        #use the 100 data point to predict
        x_input = x_input.reshape((1, n_steps,1)) #reshape the data
        y_pred = model.predict(x_input, verbose=0)
        print(y_pred[0])
        temp_input.extend(y_pred[0].tolist())
        print(len(temp_input))

        #add to the temp_input
        lst_output.extend(y_pred.tolist()) 
        i=i+1
    

print(lst_output)

In [ ]:
#start plotting the new 30 predictions
day_new=np.arange(1,151)
day_pred=np.arange(151,181)

In [ ]:
total_start = len(df_closePrice) - 150

plt.plot(day_new,scaler.inverse_transform(df_closePrice[total_start:])) #use the previous 150 data
plt.plot(day_pred,scaler.inverse_transform(lst_output))
plt.title(stock)

In [ ]:
#combine to the whole data
df3=df_closePrice.tolist()
df3.extend(lst_output)
view_point = len(df_closePrice)-50
plt.plot(df3[view_point:])

In [ ]:
#https://towardsdatascience.com/stock-market-action-prediction-with-convnet-8689238feae3
#https://towardsdatascience.com/predicting-stock-price-with-lstm-13af86a74944
#Future plan use new headline as a feature
    #challenge : how to label?